<a href="https://colab.research.google.com/github/ArfaKhalid/Computer-Vision/blob/main/SAM_remote_sensing_imagery.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
 %pip install segment-geospatial

Segment Anything Model for remote sensing imagery

In [2]:
# Import libraries
# %pip install segment-geospatial
import os
import leafmap
from samgeo import SamGeo, tms_to_geotiff, get_basemaps

Interactive Map

In [16]:
m = leafmap.Map(center=[40.676840, -98.369222], zoom=19)
m.add_basemap("SATELLITE")
m

Map(center=[40.67684, -98.369222], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

In [4]:
if m.user_roi_bounds() is not None:
    bbox = m.user_roi_bounds()
else:
    bbox = [-98.3704, 40.6762, -98.368, 40.6775]

**Map tiles and mosaic them into a single GeoTIFF file**

In [5]:
image = "satellite.tif"

**Base map as the source**

In [6]:
tms_to_geotiff(output=image, bbox=bbox, zoom=20, source="Satellite", overwrite=True)

Downloaded image 01/48
Downloaded image 02/48
Downloaded image 03/48
Downloaded image 04/48
Downloaded image 05/48
Downloaded image 06/48
Downloaded image 07/48
Downloaded image 08/48
Downloaded image 09/48
Downloaded image 10/48
Downloaded image 11/48
Downloaded image 12/48
Downloaded image 13/48
Downloaded image 14/48
Downloaded image 15/48
Downloaded image 16/48
Downloaded image 17/48
Downloaded image 18/48
Downloaded image 19/48
Downloaded image 20/48
Downloaded image 21/48
Downloaded image 22/48
Downloaded image 23/48
Downloaded image 24/48
Downloaded image 25/48
Downloaded image 26/48
Downloaded image 27/48
Downloaded image 28/48
Downloaded image 29/48
Downloaded image 30/48
Downloaded image 31/48
Downloaded image 32/48
Downloaded image 33/48
Downloaded image 34/48
Downloaded image 35/48
Downloaded image 36/48
Downloaded image 37/48
Downloaded image 38/48
Downloaded image 39/48
Downloaded image 40/48
Downloaded image 41/48
Downloaded image 42/48
Downloaded image 43/48
Downloaded 

**Display above downloaded images on the map**

**Install Localtileserver for basemap**

In [7]:
%pip install segment-geospatial leafmap localtileserver

In [17]:
m.layers[-1].visible = False  # turn off the basemap
m.add_raster(image, layer_name="Image")
m

Map(bottom=50481221.0, center=[40.67684, -98.369222], controls=(ZoomControl(options=['position', 'zoom_in_text…

Initialize SAM class

In [9]:
sam = SamGeo(
    model_type="vit_h",
    checkpoint="sam_vit_h_4b8939.pth",
    sam_kwargs=None,
)

Model checkpoint for vit_h not found.


Downloading...
From: https://dl.fbaipublicfiles.com/segment_anything/sam_vit_h_4b8939.pth
To: /root/.cache/torch/hub/checkpoints/sam_vit_h_4b8939.pth
100%|██████████| 2.56G/2.56G [00:18<00:00, 139MB/s] 


**Segment the image**
For large images that cannot fit in memory we can set the batch=True to segment the image in batches.

In [12]:
mask = "segment.tif"
sam.generate(
    image, mask, batch=True, foreground=True, erosion_kernel=(3, 3), mask_multiplier=255
)

100%|██████████| 12/12 [01:38<00:00,  8.20s/it]


**Polygonize the raster data**
Save the segmentation results as a GeoPackage file.

In [13]:
vector = "segment.gpkg"
sam.tiff_to_gpkg(mask, vector, simplify_tolerance=None)

We can also save the segmentation results as any vector data format supported by GeoPandas.

In [14]:
shapefile = "segment.shp"
sam.tiff_to_vector(mask, shapefile)

Visualize the results

In [18]:
style = {
    "color": "#3388ff",
    "weight": 2,
    "fillColor": "#7c4185",
    "fillOpacity": 0.5,
}
m.add_vector(vector, layer_name="Vector", style=style)
m

Map(bottom=25240733.0, center=[40.67684999999999, -98.36919999999999], controls=(ZoomControl(options=['positio…